Kütüphaneler eklenmesi

In [1]:
from datasets import load_dataset
import pandas as pd 
from pymongo import MongoClient
from transformers import BertTokenizer, BertForMaskedLM, DPRContextEncoderTokenizer,DPRContextEncoder;




c:\gitProjects\yeni\.venv\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Parquet dosyalarının dataframe olarak yüklenmesi(okuma yapabilmek için)

In [3]:
# Parquet dosyalarını DataFrame olarak yükleyin
train_df1 = pd.read_parquet('C:\\gitProjects\\yeni\\wikipedia-tr\\data\\train-00000-of-00002-ed6b025df7a1f653.parquet')
train_df2 = pd.read_parquet('C:\\gitProjects\\yeni\\wikipedia-tr\\data\\train-00001-of-00002-0aa63953f8b51c17.parquet')


In [4]:
# İki DataFrame'i birleştirin
merged_train = pd.concat([train_df1, train_df2], ignore_index=True)


In [5]:
# Örneğin %80 train, %20 test olarak ayırın
train_data = merged_train.sample(frac=0.8, random_state=42)
test_data = merged_train.drop(train_data.index)


In [6]:
import os

# Dosya yolları
train_dir = 'C:\\gitProjects\\yeni\\datasets\\train_Egitim'
test_dir = 'C:\\gitProjects\\yeni\\datasets\\test_Egitim'
train_file_path = os.path.join(train_dir, 'merged_train.parquet')
test_file_path = os.path.join(test_dir, 'merged_test.parquet')

# Dizinlerin var olup olmadığını kontrol etme, gerekirse oluşturma
os.makedirs(train_dir, exist_ok=True)
os.makedirs(test_dir, exist_ok=True)

# Veriyi .parquet formatında kaydetme
train_data.to_parquet(train_file_path)
test_data.to_parquet(test_file_path)

Dataframe deki bilgileri görme 

In [7]:
print(train_data.head())
print(test_data.head())

             id                                                url  \
515773  3525037  https://tr.wikipedia.org/wiki/P%C5%9F%C4%B1qo%...   
517811  3532700      https://tr.wikipedia.org/wiki/Craterolophinae   
436350  3203545           https://tr.wikipedia.org/wiki/Notocrabro   
223281  1765445    https://tr.wikipedia.org/wiki/Ibrahim%20Sissoko   
100272   575462        https://tr.wikipedia.org/wiki/Salah%20Cedid   

                  title                                               text  
515773    Pşıqo Ahecaqo  Pşıqo Ahecaqo (), Çerkes siyasetçi, askeri kom...  
517811  Craterolophinae  Craterolophinae, Depastridae familyasına bağlı...  
436350       Notocrabro  Notocrabro Crabronina oymağına bağlı bir cinst...  
223281  Ibrahim Sissoko  İbrahim Sissoko (d. 30 Kasım 1991), Fildişi Sa...  
100272      Salah Cedid  Salah Cedid (1926-1993) (Arapça: صلاح جديد) Su...  
    id                                             url        title  \
5   35       https://tr.wikipedia.org/wiki/Kar

MongoDb'ye bağlama ve bilgi çekme 

In [7]:
import pandas as pd
from pymongo import MongoClient

def get_mongodb(database_name='EgitimDatabase', train_collection_name='train', test_collection_name='test', host='localhost', port=27017):
    """
    MongoDB connection and collection selection for train and test collections.
    """
    client = MongoClient(f'mongodb://{host}:{port}/')
    
    # Veritabanını seçin
    db = client[database_name]
    
    # Train ve test koleksiyonlarını seçin
    train_collection = db[train_collection_name]
    test_collection = db[test_collection_name]
    
    return train_collection, test_collection

# Function to load dataset into MongoDB
def dataset_read(train_file_path,test_file_path):
    data_train = pd.read_parquet(train_file_path, columns=['id', 'url', 'title', 'text'])
    data_test = pd.read_parquet(test_file_path, columns=['id', 'url', 'title', 'text'])
    data_dict_train = data_train.to_dict("records")
    data_dict_test = data_test.to_dict("records")



    # Get the MongoDB collections
    train_collection, test_collection = get_mongodb(database_name='EgitimDatabase')

 

    # Insert data into MongoDB
    train_collection.insert_many(data_dict_train)
    test_collection.insert_many(data_dict_test)


    print(f" Veriler başarıyla {train_collection} MongoDb koleksiyonuna indirildi.")
    print(f" Veriler başarıyla {test_collection} MongoDb koleksiyonuna indirildi.")
    return train_collection,test_collection

# Train ve test datasetlerini MongoDB'ye yüklemek için fonksiyonu çağır
train_file_path = 'C:\\gitProjects\\bert\\datasets\\train_Egitim\\merged_train.parquet'
test_file_path = 'C:\\gitProjects\\bert\\datasets\\test_Egitim\\merged_test.parquet'

train_collection, test_collection = dataset_read(train_file_path, test_file_path)

 Veriler başarıyla Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'EgitimDatabase'), 'train') MongoDb koleksiyonuna indirildi.
 Veriler başarıyla Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'EgitimDatabase'), 'test') MongoDb koleksiyonuna indirildi.


Similarity Sentences 

In [8]:
#datasete similarity sentence yardımıyla keywords ve subheadings tanımlama 
from sklearn.feature_extraction.text import TfidfVectorizer
from sentence_transformers import SentenceTransformer


model = SentenceTransformer("emrecan/bert-base-turkish-cased-mean-nli-stsb-tr")
#text dosyasını koleksiyon üzerinden çekme 
# Database sınıfı: Veritabanı bağlantıları ve verileri çekme işlevleri
class Database:
    @staticmethod
    def get_mongodb():
        # MongoDB bağlantı bilgilerini döndürecek şekilde tanımlanmıştır.
        return 'mongodb://localhost:27017/', 'EgitimDatabase', 'train'

    @staticmethod
    def get_input_titles():
        mongo_url, db_name, collection_name = Database.get_mongodb()
        client = MongoClient(mongo_url)
        db = client[db_name]
        collection = db[collection_name]
        query = {"title": {"$exists": True}}
        cursor = collection.find(query, {"title": 1, "_id": 0})
        title_from_db = [doc['title'] for doc in cursor]
        return title_from_db
    
    @staticmethod
    def get_input_texts():
        mongo_url, db_name, collection_name = Database.get_mongodb()
        client = MongoClient(mongo_url)
        db = client[db_name]
        collection = db[collection_name]
        query = {"text": {"$exists": True}}
        cursor = collection.find(query, {"text": 1, "_id": 0})
        text_from_db = [doc['text'] for doc in cursor]
        return text_from_db


#tf-ıdf hesaplama (anahtar kelimeler için)


#IDF = log ( Dokuman Sayısı / Terimin Geçtiği Dokuman Sayısı )

#text ve title a göre keywords belirlenmesi

#------------------------------------------------------------------------------


#sbert ile alt başlıkların oluşturulması

#kümelenme ile alt başlıkların belirlenmesi 

#-------------------------------------------------------------------------------

#anahatar kelime ve alt başlıkların veri tabnaına eklnemesi 

ModuleNotFoundError: No module named 'torch.amp'

In [ ]:
#prompt oluştururak generate etmek için hazırlık

Bert Modeliyle tokenizer atama

In [ ]:
tokenizer= BertTokenizer.from_pretrained('bert-base-uncased')
model=BertForMaskedLM.from_pretrained('bert-base-uncased')

"""BERT MODELİNİ AYARLAMA

input_file: Modelin işlem yapacağı giriş dosyasının yolunu belirtir. Bu dosya, metin verilerini içermelidir.
-----------------------------------------------------------------------------------------------------------------
output_file: Modelin çıktılarının kaydedileceği dosyanın yolunu belirtir.
------------------------------------------------------------------------------------------------------------------
layers: Hangi BERT katmanlarının kullanılacağını belirler. Örneğin, "-1,-2,-3,-4" son dört katmanı ifade eder.
----------------------------------------------------------------------------------------------------------------------
bert_config_file: Önceden eğitilmiş BERT modelinin yapılandırma dosyasının yolu. Bu dosya modelin mimarisini belirler.
--------------------------------------------------------------------------------------------------------------------------
max_seq_length: Giriş sekanslarının maksimum uzunluğu. Sekanslar bu uzunluktan uzunsa kesilir, kısa ise sıfır ile doldurulur.
--------------------------------------------------------------------------------------------------------------------------------
init_checkpoint: Başlangıç ağırlıkları. Genellikle önceden eğitilmiş bir BERT modelinin ağırlıkları buradan yüklenir.
----------------------------------------------------------------------------------------------------------------------------
vocab_file: BERT modelinin eğitildiği kelime dağarcığının (vocabulary) dosya yolu. Modelin kelime parçacıklarını tanıması için gereklidir.
--------------------------------------------------------------------------------------------------------------------------------------------------
do_lower_case: Giriş metinlerinin küçük harfe mi dönüştürüleceğini belirler. Küçük harfli model için True, büyük harfli model için False olmalıdır.
-----------------------------------------------------------------------------------------------------------------------------------------------------------
batch_size: Tahminler sırasında kullanılacak veri kümesi boyutu.
--------------------------------------------------------------------------------------------------------------------------------------
use_tpu: TPU (Tensor Processing Unit) kullanılıp kullanılmayacağını belirler. True ise TPU, False ise GPU/CPU kullanılır.
--------------------------------------------------------------------------------------------------------------------------------
master: TPU kullanılıyorsa, TPU'nun ana makinesinin adresi.
---------------------------------------------------------------------------------------------------------------------------------------
num_tpu_cores: TPU kullanılacaksa, toplam TPU çekirdek sayısını belirtir.
-----------------------------------------------------------------------------------------------------------------------------------------
use_one_hot_embeddings: TPUs'da genellikle True olarak ayarlanır çünkü bu, tf.one_hot fonksiyonunu kullanarak embedding lookup işlemlerini hızlandırır. GPU/CPU kullanılıyorsa False tercih edilir."""


t5 Modeli

In [ ]:
from transformers import pipeline
from dotenv import load_dotenv
import os 
# Load model directly
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM


#tokenizer ve modelin yüklenmesi
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-small")
model = AutoModelForSeq2SeqLM.from_pretrained("google/flan-t5-small")
prompt = "Write an article about Machine Learning in Healthcare focusing on Introduction to ML and Applications in Healthcare."
#api anahtarını çevresel değişken al
api_key= os.getenv('HUGGINGFACE_API_KEY')
#env dosyasını yükleme
load_dotenv()

#---------------------------------------------------------------------------------
if api_key is None:
    raise ValueError("Apı anahtarı .env dosyasında bulunamadı")

# Başlıkları oluştur
headers = {"Authorization": f"Bearer {api_key}"}

inputs=tokenizer(prompt, return_tensors="pt")
input_sequence = "[CLS] Machine Learning in Healthcare [SEP] Introduction to ML [SEP] Applications in Healthcare [SEP] machine learning, healthcare, AI [SEP]"
#deneme data parçası
data = {
    "title": "Machine Learning in Healthcare",
    "sub_headings": ["Introduction to ML", "Applications in Healthcare"],
    "keywords": ["machine learning", "healthcare", "AI"]
}

# Girdiyi oluşturma
prompt = (
    f"Title: {data['title']}\n"
    f"Sub-headings: {', '.join(data['sub_headings'])}\n"
    f"Keywords: {', '.join(data['keywords'])}\n"
    f"Content: {input_sequence}\n"
    "Please generate a detailed article based on the above information."
)

#metin üretimi 
output_sequences = model.generate(
    inputs['input_ids'],
    max_length=300,  # Üretilecek metnin maksimum uzunluğu
    min_length=150,  # Üretilecek metnin minimum uzunluğu
    num_return_sequences=1,  # Döndürülecek metin sayısı
    do_sample=True,  # Örneklemeye izin ver
    top_k=50,  # Top-k sampling kullan
    top_p=0.95,  # Top-p sampling kullan
    repetition_penalty=1.2,  # Anlamsız tekrarları önlemek için ceza
    eos_token_id=tokenizer.eos_token_id  # Tam cümlelerin oluşturulmasını sağla
)


# Üretilen metni token'lardan çözüp string'e çevir
generated_text = tokenizer.decode(output_sequences[0], skip_special_tokens=True)

print(generated_text)
